In [1]:
import sys
sys.path.append('../')
sys.path.append('../../')
sys.path.append('../../../')

import warnings
warnings.filterwarnings('ignore')

In [2]:
import pandas as pd 
import numpy as np
import pandas_ta as ta
from tqdm import tqdm
from backtesting import Strategy, Backtest
import statistics
import scipy
from plotting import CandlePlot
from patterns import apply_patterns
import datetime as dt  
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import os
import json
from utils import utils
plt.style.use('ggplot')
import itertools

Loading BokehJS ...

In [3]:
import csv
from tqdm import tqdm
import multiprocessing as mp
import os
import pandas_ta as ta
from backtesting import Backtest, Strategy
from itertools import product
import pandas as pd
import sys
from backtesting.lib import crossover

In [5]:
pairs = ['NAS100_USD', 'SPX500_USD', 'UK100_GBP', 'DE30_EUR', 'XAU_USD', 'BCO_USD', 'CORN_USD', 'XCU_USD', 'US2000_USD', 'XAG_USD']
granualrity = ['M5', 'M15', 'M30', 'H1']
years = [2023, 2024]
FILE_NAME = 'KeltnerChannelBreakoutBacktest_24.08.2024'
FOLDER_NAME = 'discovery_testing'

In [6]:
DATA_PATH = '../../../data'

In [76]:
# Placeholder function to calculate the 200-period SMA
def calculate_sma(data, period=200):
    return ta.sma(pd.Series(data), period)


# Placeholder function to calculate the 200-period EMA
def calculate_ema(data, period=200):
    return ta.ema(pd.Series(data), period)


# Custom implementation of the MACD
def MACD(series, fast_period=12, slow_period=26, signal_period=9):
    fast_ema = calculate_ema(series, fast_period)
    slow_ema = calculate_ema(series, slow_period)
    macd_line = fast_ema - slow_ema
    signal_line = calculate_ema(macd_line, signal_period)
    histogram = macd_line - signal_line
    return macd_line, signal_line, histogram


# Custom implementation of the Average Directional Index (ADX)
def ADX(high, low, close, period=14):
    high = pd.Series(high)
    low = pd.Series(low)
    close = pd.Series(close)
    
    tr = np.maximum(
        high - low, np.maximum(abs(high - close.shift()), abs(low - close.shift()))
    )
    atr = tr.rolling(window=period).mean()

    plus_dm = high.diff()
    minus_dm = -low.diff()

    plus_dm[plus_dm < 0] = 0
    minus_dm[minus_dm < 0] = 0

    plus_di = 100 * (plus_dm.ewm(alpha=1 / period).mean() / atr)
    minus_di = 100 * (minus_dm.ewm(alpha=1 / period).mean() / atr)
    dx = (abs(plus_di - minus_di) / (plus_di + minus_di)) * 100
    adx = dx.rolling(window=period).mean()

    return adx


# Placeholder function to calculate the Keltner Channels
def calculate_keltner_channels(high, low, close, length=40):
    typical_price = (pd.Series(high) + pd.Series(low) + pd.Series(close)) / 3
    ema = typical_price.ewm(span=length, adjust=False).mean()
    atr = pd.Series(high).sub(pd.Series(low)).ewm(span=length, adjust=False).mean()
    upper_band = ema + (atr * 2)
    lower_band = ema - (atr * 2)
    return upper_band, ema, lower_band


# Placeholder function to calculate the 25-period Hull Moving Average
def calculate_hma(data, period=25):
    half_length = period // 2
    sqrt_length = int(np.sqrt(period))
    wma_half = 2 * pd.Series(data).rolling(window=half_length).mean()
    wma_full = pd.Series(data).rolling(window=period).mean()
    raw_hma = wma_half - wma_full
    hma = raw_hma.rolling(window=sqrt_length).mean()
    return hma


# Placeholder function to calculate the calculate_rsi and its 20-period calculate_sma
def calculate_rsi(data, rsi_length=14, rsi_sma_length=20):
    delta = pd.Series(data).diff(1)
    gain = delta.where(delta > 0, 0)
    loss = -delta.where(delta < 0, 0)
    avg_gain = gain.rolling(window=rsi_length).mean()
    avg_loss = loss.rolling(window=rsi_length).mean()
    rs = avg_gain / avg_loss
    rsi = 100 - (100 / (1 + rs))
    rsi_sma = rsi.rolling(window=rsi_sma_length).mean()
    return rsi, rsi_sma

# Custom implementation of the MACD
def MACD(series, fast_period=12, slow_period=26, signal_period=9):
    fast_ema = calculate_ema(series, fast_period)
    slow_ema = calculate_ema(series, slow_period)
    macd_line = fast_ema - slow_ema
    signal_line = calculate_ema(macd_line, signal_period)
    histogram = macd_line - signal_line
    return macd_line, signal_line, histogram


In [77]:
p = 'XAU_USD'
g = 'M30'
y = years[0]

df = utils.construct_df_O(p, g, y - 1, y + 1, DIRECTORY_PATH=DATA_PATH)

In [82]:
# Define the strategy class
class KeltnerChannelBreakoutStrategy(Strategy):
    # Define parameters for the strategy (can be optimized later)
    keltner_length = 40
    rsi_length = 14
    rsi_sma_length = 20
    hma_length = 25
    ma_length = 200
    units = 0.1  # Position size
    macd_enabled = False
    adx_enabled = False
    atr_filter_enabled = False
    partial_profit_enabled = False
    atr_threshold = 0.5  # ATR threshold for volatility filter
    partial_profit_level = 0.5  # Level at which to take partial profits
    
    def init(self):
        # Calculate indicators
        self.ma_200 = self.I(calculate_sma, self.data.Close, self.ma_length)
        self.rsi, self.rsi_sma = self.I(calculate_rsi, self.data.Close, self.rsi_length, self.rsi_sma_length)
        self.hma = self.I(calculate_hma, self.data.Close, self.hma_length)
        self.upper_keltner, self.middle_keltner, self.lower_keltner = self.I(calculate_keltner_channels, self.data.High, self.data.Low, self.data.Close, self.keltner_length)
        
        if self.macd_enabled:
            self.macd_line, self.signal_line, _ = self.I(MACD, self.data.Close)
        
        if self.adx_enabled:
            self.adx = self.I(ADX, self.data.High, self.data.Low, self.data.Close)
        
        if self.atr_filter_enabled:
            self.atr = self.I(ATR, self.data.High, self.data.Low, self.data.Close, 14)

    def next(self):
        # Check for MACD and ADX conditions if enabled
        macd_condition = (not self.macd_enabled) or (self.macd_line[-1] > self.signal_line[-1])
        adx_condition = (not self.adx_enabled) or (self.adx[-1] > 25)
        
        # Volatility Filter
        if self.atr_filter_enabled and self.atr[-1] < self.atr_threshold:
            return
        
        # Long Entry Conditions
        if (self.data.Close[-1] > self.ma_200[-1] and 
            self.data.Close[-1] > self.hma[-1] and 
            self.rsi[-1] > self.rsi_sma[-1] and 
            self.data.Close[-1] > self.upper_keltner[-1] and
            macd_condition and
            adx_condition):
            stop_loss = self.data.Low[-2:].min()
            self.buy(sl=stop_loss, size=self.units)

        # Short Entry Conditions
        elif (self.data.Close[-1] < self.ma_200[-1] and 
              self.data.Close[-1] < self.hma[-1] and 
              self.rsi[-1] < self.rsi_sma[-1] and 
              self.data.Close[-1] < self.lower_keltner[-1] and
              macd_condition and
              adx_condition):
            stop_loss = self.data.High[-2:].max()
            
            self.sell(sl=stop_loss, size=self.units)

        # Manage open trades
        for index in range(len(self.trades)):
            position = self.trades[index]
            # Dynamic Stop Loss
            if position.is_long:
                stop_loss = max(self.data.Low[-2:])
                if self.data.Close[-1] < stop_loss:
                    position.close()
                elif self.partial_profit_enabled:
                    if self.data.Close[-1] >= self.upper_keltner[-1] * (1 + self.partial_profit_level):
                        position.close(size=self.units / 2)
            
            if position.is_short:
                stop_loss = min(self.data.High[-2:])
                if self.data.Close[-1] > stop_loss:
                    position.close()
                elif self.partial_profit_enabled:
                    if self.data.Close[-1] <= self.lower_keltner[-1] * (1 - self.partial_profit_level):
                        position.close(size=self.units / 2)

In [83]:
bt = Backtest(df, KeltnerChannelBreakoutStrategy, cash=4000, margin=1/30, commission=.002)
stats = bt.run()

In [84]:
stats

Start                                     0.0
End                                   23605.0
Duration                              23605.0
Exposure Time [%]                    3.698212
Equity Final [$]                    524.00098
Equity Peak [$]                   4074.797496
Return [%]                         -86.899976
Buy & Hold Return [%]               12.772255
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -87.140441
Avg. Drawdown [%]                  -30.333802
Max. Drawdown Duration                23286.0
Avg. Drawdown Duration                 7775.0
# Trades                                509.0
Win Rate [%]                        15.717092
Best Trade [%]                       1.919766
Worst Trade [%]                     -1.422763
Avg. Trade [%]                    

In [81]:
bt.plot()

GridPlot(id='p1386', ...)